# Part 1 - Working with Text Data

### Use Python string methods remove irregular whitespace from the following string:

In [3]:
# All imports in one place whether I need them or not. 
import pandas as pd
import numpy as np
import re
import requests
import string
import matplotlib.pyplot as plt

from bs4 import BeautifulSoup

from collections import defaultdict
from collections import Counter

!pip install -U nltk
import nltk
nltk.download('punkt')
nltk.download('stopwords')
from nltk.tokenize import sent_tokenize # Sentence Tokenizer
from nltk.tokenize import word_tokenize # Word Tokenizer
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.probability import FreqDist

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer

Requirement already up-to-date: nltk in /anaconda3/lib/python3.6/site-packages (3.4)


[nltk_data] Downloading package punkt to
[nltk_data]     /Users/danielleromanoff/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/danielleromanoff/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [4]:
# Removing the unnessary white space to make a normal sentence
whitespace_string = '\n\n  This is a    string   that has  \n a lot of  extra \n   whitespace.   '
print(whitespace_string.strip())
print('---------------')
print(' '.join(whitespace_string.split()))

This is a    string   that has  
 a lot of  extra 
   whitespace.
---------------
This is a string that has a lot of extra whitespace.


### Use Regular Expressions to take the dates in the following .txt file and put them into a dataframe with columns for:

[RegEx dates.txt](https://github.com/ryanleeallred/datasets/blob/master/dates.txt)

- Day
- Month
- Year


In [5]:
# Bringing in the text file to use and make a df with the required information
url = 'https://raw.githubusercontent.com/ryanleeallred/datasets/master/dates.txt'
page = requests.get(url)
page = page.text
page

'March 8, 2015\r\nMarch 15, 2015\r\nMarch 22, 2015\r\nMarch 29, 2015\r\nApril 5, 2015\r\nApril 12, 2015\r\nApril 19, 2015\r\nApril 26, 2015\r\nMay 3, 2015\r\nMay 10, 2015\r\nMay 17, 2015\r\nMay 24, 2015\r\nMay 31, 2015\r\nJune 7, 2015\r\nJune 14, 2015\r\nJune 21, 2015\r\nJune 28, 2015\r\nJuly 5, 2015\r\nJuly 12, 2015\r\nJuly 19, 2015'

In [6]:
# separating Month, Day, and Year
month = re.findall(r'[a-zA-z]+', page)
day = re.findall(r'\d+', page)
day = day[::2]
year = re.findall(r'\d{4}', page)
print(month)
print(day)
print(year)

['March', 'March', 'March', 'March', 'April', 'April', 'April', 'April', 'May', 'May', 'May', 'May', 'May', 'June', 'June', 'June', 'June', 'July', 'July', 'July']
['8', '15', '22', '29', '5', '12', '19', '26', '3', '10', '17', '24', '31', '7', '14', '21', '28', '5', '12', '19']
['2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015', '2015']


In [7]:
df = pd.DataFrame({'Day':day, 'Month':month, 'Year':year})
df

Day  Month  Year
0    8  March  2015
1   15  March  2015
2   22  March  2015
3   29  March  2015
4    5  April  2015
5   12  April  2015
6   19  April  2015
7   26  April  2015
8    3    May  2015
9   10    May  2015
10  17    May  2015
11  24    May  2015
12  31    May  2015
13   7   June  2015
14  14   June  2015
15  21   June  2015
16  28   June  2015
17   5   July  2015
18  12   July  2015
19  19   July  2015

# Part 2 - Bag of Words 

### Use the twitter sentiment analysis dataset found at this link for the remainder of the Sprint Challenge:

[Twitter Sentiment Analysis Dataset](https://raw.githubusercontent.com/ryanleeallred/datasets/master/twitter_sentiment_binary.csv)

 ### Clean and tokenize the documents ensuring the following properties of the text:

1) Text should be lowercase.

2) Stopwords should be removed.

3) Punctuation should be removed.

4) Tweets should be tokenized at the word level. 

(The above don't necessarily need to be completed in that specific order.)

### Output some cleaned tweets so that we can see that you made all of the above changes.


In [8]:
# Bringing in csv from Ryan's github content
url =('https://raw.githubusercontent.com/ryanleeallred/datasets/master/twitter_sentiment_binary.csv')
twitters = requests.get(url)
twitters = twitters.text
twitters

'Sentiment,SentimentText\n0,                     is so sad for my APL friend.............\n0,                   I missed the New Moon trailer...\n1,              omg its already 7:30 :O\n0,          .. Omgaga. Im sooo  im gunna CRy. I\'ve been at this dentist since 11.. I was suposed 2 just get a crown put on (30mins)...\n0,         i think mi bf is cheating on me!!!       T_T\n0,         or i just worry too much?        \n1,       Juuuuuuuuuuuuuuuuussssst Chillin!!\n0,       Sunny Again        Work Tomorrow  :-|       TV Tonight\n1,      handed in my uniform today . i miss you already\n1,      hmmmm.... i wonder how she my number @-)\n0,      I must think about positive..\n1,      thanks to all the haters up in my face all day! 112-102\n0,      this weekend has sucked so far\n0,     jb isnt showing in australia any more!\n0,     ok thats it you win.\n0,    &lt;-------- This is the way i feel right now...\n0,"    awhhe man.... I\'m completely useless rt now. Funny, all I can do is twit

In [10]:
table = str.maketrans('','', string.punctuation)
stop_words = set(stopwords.words('english'))

cleaned_listings = []

for listing in twitters:
  # Tokenize by word
  tokens = word_tokenize(listing)
  # Make all words lowercase
  lowercase_tokens = [w.lower() for w in tokens]
  # Strip punctuation from within words
  no_punctuation = [x.translate(table) for x in lowercase_tokens]
  # Remove words that aren't alphabetic
  alphabetic = [word for word in no_punctuation if word.isalpha()]
  # Remove stopwords
  words = [w for w in alphabetic if not w in stop_words]
  # Append to list
  cleaned_listings.append(words)

KeyboardInterrupt: 

### How should TF-IDF scores be interpreted? How are they calculated?

#### Your Answer Here #####

# Part 3 - Document Classification

1) Use Train_Test_Split to create train and test datasets.

2) Vectorize the tokenized documents using your choice of vectorization method. 

 - Stretch goal: Use both of the methods that we talked about in class.

3) Create a vocabulary using the X_train dataset and transform both your X_train and X_test data using that vocabulary.

4) Use your choice of binary classification algorithm to train and evaluate your model's accuracy. Report both train and test accuracies.

 - Stretch goal: Use an error metric other than accuracy and implement/evaluate multiple classifiers.



In [ ]:
##### Your Code Here #####

# Part 4 -  Word2Vec

1) Fit a Word2Vec model on your cleaned/tokenized twitter dataset. 

2) Display the 10 words that are most similar to the word "twitter"

In [ ]:
##### Your Code Here #####